# How does an artist become my favorite artist?

In [3]:
# IPython magic to autoreload imports
%load_ext autoreload
%autoreload 2

In [4]:
import pandas as pd
import plotly.express as px
import chart_studio
import chart_studio.plotly as py

from streaming_history import StreamETL

In [136]:
username = 'rvallejov' # your username
api_key = 'x2Udz3jytnODjroDMTaw' # your api key - go to profile > settings > regenerate key
chart_studio.tools.set_credentials_file(username=username, api_key=api_key)

Initalize ETL instance

In [5]:
etl = StreamETL()

## Get the data

In [6]:
# etl.get_streams(track_limit=10000, get_audio_features=False)
# etl.get_streams(get_audio_features=False)

## Clean the data - _Silver_

In [7]:
df_bronze = pd.read_csv('data/bronze/2024_10_13_lastfm_spotify_audio_features.csv',
                        parse_dates=['stream_date'])
etl.clean_streams(df_bronze)

Saved 109000 tracks to data/silver/2024_10_13_lastfm_spotify_audio_features.csv


In [10]:
df_bronze.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 109000 entries, 0 to 108999
Data columns (total 4 columns):
 #   Column       Non-Null Count   Dtype         
---  ------       --------------   -----         
 0   stream_date  109000 non-null  datetime64[ns]
 1   track        109000 non-null  object        
 2   artist       109000 non-null  object        
 3   album        108982 non-null  object        
dtypes: datetime64[ns](1), object(3)
memory usage: 3.3+ MB


In [152]:
df_silver = pd.read_csv('data/silver/2024_10_13_lastfm_spotify_audio_features.csv',
                        parse_dates=['stream_date','stream_month'])
df_silver.sort_values('stream_date').head(20)

stream_date                               track  \
108999 2017-10-12 14:06:00                     No Ordinary Man   
108998 2017-10-12 14:10:00        Always There When I Need You   
108997 2017-10-12 14:15:00                          Good Winds   
108996 2017-10-12 14:19:00                           Holy Soul   
108995 2017-10-12 14:23:00                   Run For The Money   
108994 2017-10-12 14:26:00                            Oom Velt   
108993 2017-10-12 14:28:00                       The Finishing   
108992 2017-10-12 14:36:00                    Chasing Sunshine   
108991 2017-10-12 14:48:00  Fade Out Lines - The Avener Rework   
108990 2017-10-12 14:54:00                   Billionth Remnant   
108989 2017-10-12 14:59:00              Your Heart Sounds Like   
108988 2017-10-12 15:03:00                                  Eh   
108987 2017-10-12 15:08:00                   Already Know That   
108986 2017-10-12 15:20:00                             A River   
108985 2017-10-12 15:24:00      But Now A Warm Feel Is Running   
108984 2017-10-12 15:29:00                         Those Waves   
108983 2017-10-12 15:35:00                   One of These Days   
108982 2017-10-12 15:41:00                        Jolie Banane   
108981 2017-10-12 15:47:00                        Keep Me Home   
108980 2017-10-12 15:55:00                              5 to 4   

                              artist                         album  \
108999                Salt Cathedral               No Ordinary Man   
108998                Salt Cathedral  Always There When I Need You   
108997                Salt Cathedral                      Oom Velt   
108996                Salt Cathedral                      Oom Velt   
108995                Salt Cathedral             Run For The Money   
108994                Salt Cathedral                      Oom Velt   
108993                       Stavroz                   The Ginning   
108992               Maya Jane Coles                   Take Flight   
108991  The Avener & Phoebe Killdeer  The Wanderings of the Avener   
108990                        Geotic                        Abysma   
108989                          Fhin           A Crack in the Eyes   
108988                          Fhin           A Crack in the Eyes   
108987                          Fhin           A Crack in the Eyes   
108986                          Fhin           A Crack in the Eyes   
108985                          Fhin           A Crack in the Eyes   
108984                          Fhin           A Crack in the Eyes   
108983                 Kraak & Smaak    Boogie Angst (Bonus Remix)   
108982                 Kraak & Smaak    Boogie Angst (Bonus Remix)   
108981                 Kraak & Smaak    Boogie Angst (Bonus Remix)   
108980                 Kraak & Smaak    Boogie Angst (Bonus Remix)   

              stream_month     artist_clean  
108999 2017-10-01 14:06:00            Other  
108998 2017-10-01 14:10:00            Other  
108997 2017-10-01 14:15:00            Other  
108996 2017-10-01 14:19:00            Other  
108995 2017-10-01 14:23:00            Other  
108994 2017-10-01 14:26:00            Other  
108993 2017-10-01 14:28:00          Stavroz  
108992 2017-10-01 14:36:00  Maya Jane Coles  
108991 2017-10-01 14:48:00            Other  
108990 2017-10-01 14:54:00           Geotic  
108989 2017-10-01 14:59:00             Fhin  
108988 2017-10-01 15:03:00             Fhin  
108987 2017-10-01 15:08:00             Fhin  
108986 2017-10-01 15:20:00             Fhin  
108985 2017-10-01 15:24:00             Fhin  
108984 2017-10-01 15:29:00             Fhin  
108983 2017-10-01 15:35:00    Kraak & Smaak  
108982 2017-10-01 15:41:00    Kraak & Smaak  
108981 2017-10-01 15:47:00    Kraak & Smaak  
108980 2017-10-01 15:55:00    Kraak & Smaak

In [15]:
etl.aggregate_data(df_silver)

Saved 32948 rows to data/gold/2024_10_13_aggregate_streams.csv


#### ✅ Descriptive metrics

In [21]:
n_plays = len(df_silver)
n_unique_artists = df_silver.artist.nunique()

In [22]:
df_summary_full_history = df_silver.groupby('artist').track.count().sort_values(ascending=False).reset_index()
df_summary_full_history = df_summary_full_history.rename(columns={'track': 'play_count'}, inplace=False)

In [23]:
df_summary_full_history['rel_play_count'] = df_summary_full_history.play_count / n_plays
df_summary_full_history['cumulative_rel_play_count'] = df_summary_full_history.rel_play_count.cumsum()

In [24]:
n_artists_80_perc = len(df_summary_full_history.query("cumulative_rel_play_count < 0.8"))
perc_artists_80_perc = round(n_artists_80_perc / n_unique_artists * 100)
print(f'80% of plays belong to {n_artists_80_perc} artists. This represents {perc_artists_80_perc}% of a total of {n_unique_artists} unique streamed atrists')

80% of plays belong to 765 artists. This represents 13% of a total of 5862 unique streamed atrists


In [27]:
df_summary_full_history.head(20)

artist  play_count  rel_play_count  \
0              Khruangbin        1567        0.014376   
1         LCD Soundsystem        1420        0.013028   
2               Radiohead        1052        0.009651   
3           L'Impératrice         941        0.008633   
4             Tame Impala         857        0.007862   
5                    DIIV         852        0.007817   
6                  Jungle         797        0.007312   
7    Thievery Corporation         743        0.006817   
8               The Blaze         723        0.006633   
9               Roosevelt         714        0.006550   
10           The National         706        0.006477   
11                Parcels         685        0.006284   
12          Local Natives         679        0.006229   
13            Royal Blood         674        0.006183   
14          Still Corners         652        0.005982   
15  Red Hot Chili Peppers         649        0.005954   
16               Darkside         641        0.005881   
17                Santana         608        0.005578   
18               Poolside         570        0.005229   
19  The Chemical Brothers         566        0.005193   

    cumulative_rel_play_count  
0                    0.014376  
1                    0.027404  
2                    0.037055  
3                    0.045688  
4                    0.053550  
5                    0.061367  
6                    0.068679  
7                    0.075495  
8                    0.082128  
9                    0.088679  
10                   0.095156  
11                   0.101440  
12                   0.107670  
13                   0.113853  
14                   0.119835  
15                   0.125789  
16                   0.131670  
17                   0.137248  
18                   0.142477  
19                   0.147670

In [153]:
# Create a cumulative distribution plot using Plotly
fig = px.ecdf(df_summary_full_history, 
              x='play_count', 
              title='Cumulative Distribution of Play Count',
              labels={'play_count': 'Play Count'})

# Show the plot
fig.show()

In [154]:
py.plot(fig, filename = 'ecdf_play_count_by_artist', auto_open=True)

'https://plotly.com/~rvallejov/5/'

In [155]:
# Create a box & whiskers plot on top of a swarm plot using Plotly
# fig = px.box(df_summary_full_history, 
#              y='play_count', 
#              hover_data=['artist'],
#              points='all',  # This adds the swarm plot
#              title='Box & Whiskers Plot with Swarm Plot of Play Count',
#              labels={'play_count': 'Play Count'}
#              )

# Create a box & whiskers plot on top of a swarm plot using Plotly
fig = px.strip(df_summary_full_history, 
             y='play_count', 
             hover_data=['artist'],
             title='Swarm Plot of Play Count',
             labels={'play_count': 'Play Count'}
             )

# Show the plot
fig.show()

In [156]:
py.plot(fig, filename = 'swarm_play_count_by_artist', auto_open=True)

'https://plotly.com/~rvallejov/7/'

In [140]:
top_artists = df_summary_full_history.nlargest(50, columns='play_count').artist.tolist()
top_artists

['Khruangbin',
 'LCD Soundsystem',
 'Radiohead',
 "L'Impératrice",
 'Tame Impala',
 'DIIV',
 'Jungle',
 'Thievery Corporation',
 'The Blaze',
 'Roosevelt',
 'The National',
 'Parcels',
 'Local Natives',
 'Royal Blood',
 'Still Corners',
 'Red Hot Chili Peppers',
 'Darkside',
 'Santana',
 'Poolside',
 'The Chemical Brothers',
 'Air',
 'Lee Burridge',
 'The Rapture',
 'Papooz',
 'HVOB',
 'Paradis',
 'Underworld',
 'Foals',
 'M83',
 'The War on Drugs',
 'Kerala Dust',
 'Sufjan Stevens',
 'Whitney',
 'Kikagaku Moyo',
 'Polo & Pan',
 'Ichisan',
 'Slowdive',
 'Lane 8',
 'Trent Reznor and Atticus Ross',
 'Broken Bells',
 'Hermanos Gutiérrez',
 'Ten Fé',
 'The Verve',
 'Mac Miller',
 'Cut Copy',
 'FEWS',
 'Against All Logic',
 'The Weeknd',
 'Moderat',
 'Bicep']

## Aggregate the data - _Gold_

In [16]:
df_gold = pd.read_csv('data/gold/2024_10_13_aggregate_streams.csv',
                      parse_dates=['stream_date','stream_month'])

# df_gold['cumulative_play_count'] = df_gold.sort_values('stream_date').groupby('artist_clean').play_count.cumsum()
df_gold.head().T

0                    1  \
stream_date              2017-10-12 00:00:00  2017-10-12 00:00:00   
artist_clean                     Barry White                Bicep   
play_count                                11                    1   
stream_month             2017-10-01 00:00:00  2017-10-01 00:00:00   
cumulative_play_count                     11                    1   
first_stream_date                 2017-10-12           2017-10-12   
days_since_first_stream                    0                    0   

                                           2                    3  \
stream_date              2017-10-12 00:00:00  2017-10-12 00:00:00   
artist_clean                            DBFC                 Fhin   
play_count                                 1                    6   
stream_month             2017-10-01 00:00:00  2017-10-01 00:00:00   
cumulative_play_count                      1                    6   
first_stream_date                 2017-10-12           2017-10-12   
days_since_first_stream                    0                    0   

                                           4  
stream_date              2017-10-12 00:00:00  
artist_clean                   Fleetwood Mac  
play_count                                 2  
stream_month             2017-10-01 00:00:00  
cumulative_play_count                      2  
first_stream_date                 2017-10-12  
days_since_first_stream                    0

### 📊 Time series by artist by mnothly play count

In [148]:
df_plot = df_gold.query("artist_clean != 'Other'").copy()
df_plot = df_plot.groupby(['stream_month','artist_clean']).play_count.sum().reset_index()
# df_plot = df_plot[df_plot.artist_clean.isin(top_artists)]

# Create a stacked bar chart using Plotly
fig = px.line(df_plot, 
             x='stream_month', 
             y='play_count', 
             color='artist_clean',
             markers=True,
             title='Time Series of Top Artists by Play Count',
             labels={'stream_date': 'Date', 'play_count': 'Number of Plays'}
             )

# Show the plot
fig.show()

In [149]:
py.plot(fig, filename = 'time_series_monthly_plays_by_artist', auto_open=True)

'https://plotly.com/~rvallejov/3/'

### 📊 Bar chart by artist by monthly play count

In [157]:
df_plot = df_gold.query("artist_clean != 'Other'").copy()
df_plot = df_plot.groupby(['stream_month','artist_clean']).play_count.sum().reset_index()
# df_plot = df_plot[df_plot.artist_clean.isin(top_artists)]

# Create a stacked bar chart using Plotly
fig = px.bar(df_plot, 
             x='stream_month', 
             y='play_count', 
             color='artist_clean',
             title='Stacked Bar Chart of Top Artists by Play Count',
             labels={'stream_date': 'Date', 'play_count': 'Number of Plays'}
             )

# Show the plot
fig.show()

In [ ]:
py.plot(fig, filename = 'bar_chart_monthly_plays_by_artist', auto_open=True)

### 📊 Time Series by artist by **cumulative** play count

In [141]:
# Compute the cumulative play count and plot a time series
# df_plot = df_gold.copy()
df_plot = df_gold.query("artist_clean != 'Other'").copy()
df_plot = df_plot[df_plot.artist_clean.isin(top_artists)]

# Create a time series plot using Plotly
fig = px.line(df_plot, 
              x='stream_date', 
              y='cumulative_play_count', 
              color='artist_clean',
              title='Time Series of Top Artists by Play Count',
              labels={'stream_date': 'Date', 'play_count': 'Number of Plays'},
              markers=True)

# Show the plot
fig.show()

In [142]:
py.plot(fig, filename = 'time_series_cumulative_plays_by_artist', auto_open=True)

'https://plotly.com/~rvallejov/1/'

### 📊 Cohort Analysis by artist by DOS (Days of Streaming)

In [124]:
# Create a time series plot using Plotly
fig = px.line(df_gold, 
              x='days_since_first_stream', 
              y='cumulative_play_count', 
              color='artist_clean',
              title='Time Series of Top Artists by Play Count',
              labels={'stream_date': 'Date', 'play_count': 'Number of Plays'},
              markers=True)

# Show the plot
fig.show()

### 📊 Chart of number of days to X number of  plays

In [158]:
# Minimum number of plays to consider an artist
# min_plays = 36 # top 10% of artists
# min_plays = 77 # top 5% of artists
min_plays = 175 # top 2% of artists
# min_plays = 327 # top 1% of artists

plot_top_artists = df_summary_full_history.query(f"play_count >= {min_plays}").artist.tolist()

df_plot = df_gold.query("artist_clean != 'Other'").copy()
df_plot = df_plot[df_plot.artist_clean.isin(plot_top_artists)]
df_plot = df_plot[df_plot.cumulative_play_count <= min_plays]

# Create a time series plot using Plotly
fig = px.line(df_plot, 
              x='days_since_first_stream', 
              y='cumulative_play_count', 
              color='artist_clean',
              title='Time Series of Top Artists by Play Count',
              labels={'stream_date': 'Date', 'play_count': 'Number of Plays'},
              markers=True)

# Show the plot
fig.show()

In [159]:
# Create a time series plot using Plotly
fig = px.line(df_plot, 
              x='stream_date', 
              y='cumulative_play_count', 
              color='artist_clean',
              title='Time Series of Top Artists by Play Count',
              labels={'stream_date': 'Date', 'play_count': 'Number of Plays'},
              markers=True)

# Show the plot
fig.show()

### 📊 Top 5 artists my month

In [160]:
df_gold['stream_quarter'] = df_gold.stream_date.dt.to_period('Q')
df_gold['stream_year'] = df_gold.stream_date.dt.year
# Convert the 'stream_quarter' column to datetime format
df_gold['stream_quarter'] = df_gold['stream_quarter'].apply(lambda x: pd.to_datetime(x.start_time))
df_gold.sample(5)

stream_date artist_clean  play_count stream_month  \
26962  2023-01-02          Air           1   2023-01-01   
29096  2023-09-27        Other           5   2023-09-01   
31813  2024-05-21  James Blake           3   2024-05-01   
23950  2022-01-20       Jungle           7   2022-01-01   
24094  2022-02-05   Jamiroquai           1   2022-02-01   

       cumulative_play_count first_stream_date  days_since_first_stream  \
26962                    256        2017-11-01                     1888   
29096                  26291        2017-10-12                     2176   
31813                    272        2017-10-16                     2409   
23950                    606        2017-12-05                     1507   
24094                     47        2018-03-10                     1428   

       stream_year stream_quarter  
26962         2023     2023-01-01  
29096         2023     2023-07-01  
31813         2024     2024-04-01  
23950         2022     2022-01-01  
24094         2022     2022-01-01

In [178]:
param_top_artists = 10
period = 'stream_year'

df_artist_month = df_gold.query("artist_clean != 'Other'").copy()
df_artist_month = df_artist_month.groupby([f'{period}','artist_clean']).play_count.sum().reset_index()

# Sort the dataframe by stream_month and play_count in descending order
df_artist_period_sorted = df_artist_month.sort_values([f'{period}', 'play_count'], ascending=[True, False])

# Group by stream_month and select the top 5 artists for each month
df_top_artists_per_period = df_artist_period_sorted.groupby(f'{period}').head(param_top_artists)
# Order the colors by play_count so that the most played artist is at the top of the stacked bar
df_top_artists_per_period['artist_clean'] = pd.Categorical(df_top_artists_per_period['artist_clean'], 
                                                           categories=df_top_artists_per_period.groupby('artist_clean')['play_count'].sum().sort_values(ascending=False).index, 
                                                           ordered=True)

# Create a stacked bar chart using Plotly with ordered colors
fig = px.bar(df_top_artists_per_period, 
             x=f'{period}', 
             y='play_count', 
             color='artist_clean',
             title='Stacked Bar Chart of Top Artists by Play Count',
             labels={'stream_date': 'Date', 'play_count': 'Number of Plays'},
             category_orders={'artist_clean': df_top_artists_per_period['artist_clean'].cat.categories.tolist()}
             )

# Show the plot
fig.show()

/var/folders/l5/5qp5q725703d53br1r3lbwtw0000gn/T/ipykernel_75090/954839261.py:13: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [179]:
py.plot(fig, filename = 'bar_chart_most_streamed_artists_by_year', auto_open=True)

'https://plotly.com/~rvallejov/9/'

In [192]:
df_top_artists_per_period.sample(5)

stream_year       artist_clean  play_count
35           2017               DBFC          69
2374         2023  Layo & Bushwacka!         131
99           2017    LCD Soundsystem         193
732          2019         Khruangbin         761
1823         2022              Bicep         142

In [183]:
# Group by artist and count the number of quarters they appear in the top 5
top_artists_by_quarter = df_top_artists_per_period.groupby('artist_clean').size().reset_index(name='times_in_top_list')
top_artists_by_quarter = top_artists_by_quarter.sort_values('times_in_top_list', ascending=False)
top_artists_by_quarter.head(20)

artist_clean  times_in_top_list
0           Khruangbin                  6
2                 DIIV                  4
1      LCD Soundsystem                  3
4            Radiohead                  3
5          Royal Blood                  3
6            Roosevelt                  3
7              Parcels                  3
13       Local Natives                  2
24        Fred again..                  2
19                 Air                  2
15          Polo & Pan                  2
17       Magdalena Bay                  2
10        Lee Burridge                  2
9               Jungle                  2
3        L'Impératrice                  2
11  Hermanos Gutiérrez                  2
8          The Rapture                  2
50                DBFC                  1
42         Andrew Bird                  1
36               Bicep                  1

In [189]:
# Group by stream_year and artist_clean, then sum the play_count
df_yearly_artist = df_gold.groupby(['stream_year', 'artist_clean']).play_count.sum().reset_index()

# Calculate the total play count for each year
total_play_count_per_year = df_yearly_artist.groupby('stream_year').play_count.transform('sum')

# Calculate the relative play count
df_yearly_artist['rel_play_count'] = df_yearly_artist.play_count / total_play_count_per_year

# Filter df_yearly_artist for artists within top_artists_by_quarter
df_yearly_artist = df_yearly_artist[df_yearly_artist['artist_clean'].isin(top_artists_by_quarter['artist_clean'])]

In [191]:
# Display the dataframe
df_yearly_artist.tail(20)

stream_year           artist_clean  play_count  rel_play_count
2838         2024               Poolside          14        0.001430
2841         2024                  Powel           6        0.000613
2846         2024              Radiohead          99        0.010109
2849         2024  Red Hot Chili Peppers          28        0.002859
2855         2024              Roosevelt          34        0.003472
2856         2024            Royal Blood          28        0.002859
2862         2024                Santana          27        0.002757
2872         2024               Slowdive          53        0.005412
2879         2024          Still Corners          85        0.008680
2887         2024            Tame Impala          36        0.003676
2895         2024              The Blaze          50        0.005106
2897         2024  The Chemical Brothers          25        0.002553
2911         2024           The National           6        0.000613
2914         2024            The Rapture          16        0.001634
2920         2024              The Verve          15        0.001532
2927         2024   Thievery Corporation          63        0.006433
2928         2024             Todd Terje           3        0.000306
2933         2024           Trentemøller          16        0.001634
2937         2024             Underworld          86        0.008782
2948         2024             Widowspeak         105        0.010722

Upload plot to chart studio (plotly account)

In [ ]:
py.plot(fig, filename = 'time_series_top_artists', auto_open=True)

In [12]:
df_streams = df_streams.query("stream_date != 'now playing'")
df_streams['stream_date'] = pd.to_datetime(df_streams['stream_date'], format='%d %b %Y, %H:%M')
df_streams.head().T

1  ...                                                  5
stream_date                                     2024-10-11 15:50:00  ...                                2024-10-11 14:48:00
track                                                    simply are  ...                                                War
artist                                                       Papooz  ...                            Hypnotic Brass Ensemble
album                                                   Green Juice  ...                            Hypnotic Brass Ensemble
danceability                                                  0.763  ...                                              0.687
energy                                                         0.65  ...                                              0.628
key                                                               5  ...                                                  6
loudness                                                    -11.611  ...                                             -9.265
mode                                                              1  ...                                                  1
speechiness                                                  0.0646  ...                                              0.268
acousticness                                                  0.108  ...                                              0.541
instrumentalness                                             0.0508  ...                                              0.879
liveness                                                      0.158  ...                                              0.398
valence                                                       0.826  ...                                               0.84
tempo                                                        99.379  ...                                              96.71
type                                                 audio_features  ...                                     audio_features
id                                           2bNj1aObQceCIm5zbeySM5  ...                             5bJ1K78btQIh5gR1MaFXt0
uri                            spotify:track:2bNj1aObQceCIm5zbeySM5  ...               spotify:track:5bJ1K78btQIh5gR1MaFXt0
track_href        https://api.spotify.com/v1/tracks/2bNj1aObQceC...  ...  https://api.spotify.com/v1/tracks/5bJ1K78btQIh...
analysis_url      https://api.spotify.com/v1/audio-analysis/2bNj...  ...  https://api.spotify.com/v1/audio-analysis/5bJ1...
duration_ms                                                  236985  ...                                             173693
time_signature                                                    4  ...                                                  4

[22 rows x 5 columns]

In [29]:
#df_streams.to_csv('data/sandbox/20241011_stream_sample.csv')
top_artists = df_streams.groupby('artist').size().nlargest(20).index.tolist()
print(top_artists)

['One Sentence. Supervisor', 'The Smile', 'American Football', 'Hermanos Gutiérrez', 'Weval', 'Radiohead', 'Godspeed You! Black Emperor', 'Sub Sub', 'English Teacher', 'Guy J', 'Hypnotic Brass Ensemble', 'Jamie xx', 'Nilüfer Yanya', 'Aphex Twin', 'BDRMM', 'Cola', 'Led Zeppelin', 'Lee Burridge', 'Papooz', 'Surf Rock is Dead']


In [25]:
df_streams['artist_clean'] = df_streams.artist.apply(lambda x: x if x in top_artists else 'Other')

In [31]:
# Convert the 'stream_date' column to datetime format for proper grouping
df_streams['stream_date'] = pd.to_datetime(df_streams['stream_date'])

# Group by date (stream_date) and artist, then count the number of rows per group
grouped_df = df_streams.groupby([df_streams['stream_date'].dt.date, 'artist_clean']).size().reset_index(name='play_count')

# Display the grouped dataframe
grouped_df.head().T

0                1  ...              3           4
stream_date   2024-10-05       2024-10-05  ...     2024-10-05  2024-10-05
artist_clean        Cola  English Teacher  ...  Nilüfer Yanya       Other
play_count             2                1  ...              2           2

[3 rows x 5 columns]

In [33]:
# Create a time series plot using Plotly
fig = px.line(grouped_df, 
              x='stream_date', 
              y='play_count', 
              color='artist_clean',
              title='Time Series of Top Artists by Play Count',
              labels={'stream_date': 'Date', 'play_count': 'Number of Plays'},
              markers=True)

# Show the plot
fig.show()